In [58]:
import os
import datetime
from pathlib import Path

import pandas as pd
import numpy as np
import shapefile
import pupygrib
import ogr
from osgeo import gdal
from netCDF4 import Dataset

In [59]:
class Analysis:
    ELEMENTS = ['O3', 'NO2', 'CO']

    def __init__(self):
        self.project_folder = Path(os.path.abspath('')).parent
        self.data_folder = self.project_folder / 'data'
        self.shp_folder = self.data_folder / 'shp'
        self.nc_folder = self.data_folder / 'nc'
        # self.grib_folder = self.data_folder / 'grib'

        self.grib = []
        self.shp = []


    # def get_data(self, date: datetime.date = None):
    #     """
    #     Get shapefile(s) by date, if provided, or all of them in data folder.
    #
    #     :param date: datetime.date, when flight took place, mentioned in
    #     shapefiles names
    #     """
    #     self.shp = []
    #
    #     if date:
    #         date_str =  date.strftime("%Y%m%d")
    #         for file_ in self.shp_folder.iterdir():
    #             if date_str in file_.name and file_.suffix == '.shp':
    #                 self._get_shp(file_)
    #                 break
    #     else:
    #         for file_ in self.shp_folder.iterdir():
    #             self._get_shp(file_)

    # def _get_shp(self, file_):
    #     with shapefile.Reader(str(file_)) as shp_file:
    #         self.shp.append(shp_file)

    # def get_grib(self, file_, date: datetime.datetime):
    #     self.grib = []
    #
    #     date_str = date.strftime("%Y%m%d%H")
    #     if date_str in file_.name:
    #         with file_.open() as grib_file:
    #             grib, = pupygrib.read(grib_file)
    #         self.grib.append(grib)


#     def get_nc(self, file_, date: datetime.datetime, element: str):
#         date_str = date.strftime("%Y%m%d")
#         if date_str in file_.name and element in file_.name:
#             return netcdf.netcdf_file(file_, 'r')

    def analyse(self, date: datetime.date = None):
        # Get data
        # self.get_data()
        
        data = []
        if date:
            date_str = date.strftime("%Y%m%d")
            for file_ in self.shp_folder.iterdir():
                if date_str in file_.name and file_.suffix == '.shp':
                    with shapefile.Reader(str(file_)) as shp_file:
                        # self.shp.append(shp_file)

                        records = shp_file.records()
                        fields = shp_file.fields[1:]
                        fields_names = [field[0] for field in fields]

                        data = pd.DataFrame(
                            np.array(records), columns=fields_names
                        )
                        data[['StdAltitu']] /= 3.281  # ft to meters

                        points_x = np.empty(len(records))
                        points_y = np.empty(len(records))

                        shp = ogr.Open(str(file_.absolute()))
                        layer = shp.GetLayer()
                        i = 0
                        while i < len(records):
                            point = layer.GetFeature(i)
                            geom = point.GetGeometryRef()
                            points_x[i] = geom.GetPoint(0)[0]
                            points_y[i] = geom.GetPoint(0)[1]
                            i += 1

                        data['lat'] = points_x
                        data['long'] = points_y

                        for element in self.ELEMENTS:
                            data_clean = data.dropna(axis=1, how='all')
                            if element not in data_clean.columns:
                                continue
                            
                            data_clean = data_clean.dropna(how='any', axis=0, subset=[element])
                            print(data_clean)

                            for index, row in data_clean.iterrows():
                                nc_date = datetime.datetime.combine(date, datetime.datetime.min.time())
                                nc_date += datetime.timedelta(seconds=row['TimeCRef'])
                                nc_date_str = date.strftime("%Y%m%d")
                                
                                for file_ in self.nc_folder.iterdir():
                                    if date_str in file_.name and element in file_.name:
                                        with Dataset(str(file_), 'r', format='NETCDF4') as nc:
                                            
#                                             print(dir(nc))
                                            print(nc.variables)
                                            
                                        break
                                        
                                            #print(len(nc.dimensions))
                                    
                                if not nc:
                                    raise ValueError(f'No appropriate nc file for date: {nc_date}. Element: {element}')
                            

        return data

In [60]:
project_folder = Path(os.path.abspath('')).parent
data_folder = project_folder / 'data'
for file_ in data_folder.iterdir():
    print(file_.name)

nc
grib
original
shp
ENSEMBLE-FORECAST_CO_2019-03-28T00:00:00Z-2019-03-28T02:00:00Z_1000_Ukraine.grib
fastsheets


In [61]:
a = Analysis()
d = a.analyse(datetime.date(2015, 10, 5))

     TimeCRef StdAltitu BaroAltit  Ozone     CO     CH4 CH4_Err     lat  \
87      75925   7947.82   26042.6  34.76  72.01  1852.3     2.9  10.814   
88      75935   7980.28   26149.1  35.09  70.57  1852.8     2.4  10.800   
89      75945   8011.37   26251.1  35.38  70.37  1850.7       2  10.785   
90      75955   8040.81   26347.8  36.13  71.09  1850.7     2.4  10.770   
91      75965   8072.14   26450.4  35.78  70.34  1851.3     1.4  10.755   
92      75975    8103.9   26554.8   36.5  69.79  1852.2     2.2  10.740   
93      75985   8135.45     26658   36.9  70.48  1850.1       2  10.725   
94      75995   8166.47     26760  36.87  71.72  1850.2     1.5  10.710   
95      76005   8197.17   26860.8  36.47  69.81  1852.8     1.7  10.695   
96      76015   8228.35     26963   36.3  69.85  1852.8     2.1  10.680   
97      76025   8259.74     27066  36.25  70.84  1849.8     2.8  10.665   
98      76035   8290.89   27168.3  36.64  70.15  1850.5     1.7  10.650   
99      76045   8321.09  

OrderedDict([('time', <class 'netCDF4._netCDF4.Variable'>
float64 time(time)
    standard_name: time
    units: hours since 2015-10-5 00:00:00
    calendar: proleptic_gregorian
    axis: T
    long_name: FORECAST time from 20151005
unlimited dimensions: time
current shape = (25,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lon', <class 'netCDF4._netCDF4.Variable'>
float64 lon(lon)
    standard_name: longitude
    long_name: longitude
    units: degrees_east
    axis: X
unlimited dimensions: 
current shape = (700,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lat', <class 'netCDF4._netCDF4.Variable'>
float64 lat(lat)
    standard_name: latitude
    long_name: latitude
    units: degrees_north
    axis: Y
unlimited dimensions: 
current shape = (400,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('height', <class 'netCDF4._netCDF4.Variable'>
float64 height(height)
    standard_name: height
    long_name: height
    units: m
   

OrderedDict([('time', <class 'netCDF4._netCDF4.Variable'>
float64 time(time)
    standard_name: time
    units: hours since 2015-10-5 00:00:00
    calendar: proleptic_gregorian
    axis: T
    long_name: FORECAST time from 20151005
unlimited dimensions: time
current shape = (25,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lon', <class 'netCDF4._netCDF4.Variable'>
float64 lon(lon)
    standard_name: longitude
    long_name: longitude
    units: degrees_east
    axis: X
unlimited dimensions: 
current shape = (700,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lat', <class 'netCDF4._netCDF4.Variable'>
float64 lat(lat)
    standard_name: latitude
    long_name: latitude
    units: degrees_north
    axis: Y
unlimited dimensions: 
current shape = (400,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('height', <class 'netCDF4._netCDF4.Variable'>
float64 height(height)
    standard_name: height
    long_name: height
    units: m
   

OrderedDict([('time', <class 'netCDF4._netCDF4.Variable'>
float64 time(time)
    standard_name: time
    units: hours since 2015-10-5 00:00:00
    calendar: proleptic_gregorian
    axis: T
    long_name: FORECAST time from 20151005
unlimited dimensions: time
current shape = (25,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lon', <class 'netCDF4._netCDF4.Variable'>
float64 lon(lon)
    standard_name: longitude
    long_name: longitude
    units: degrees_east
    axis: X
unlimited dimensions: 
current shape = (700,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lat', <class 'netCDF4._netCDF4.Variable'>
float64 lat(lat)
    standard_name: latitude
    long_name: latitude
    units: degrees_north
    axis: Y
unlimited dimensions: 
current shape = (400,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('height', <class 'netCDF4._netCDF4.Variable'>
float64 height(height)
    standard_name: height
    long_name: height
    units: m
   

OrderedDict([('time', <class 'netCDF4._netCDF4.Variable'>
float64 time(time)
    standard_name: time
    units: hours since 2015-10-5 00:00:00
    calendar: proleptic_gregorian
    axis: T
    long_name: FORECAST time from 20151005
unlimited dimensions: time
current shape = (25,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lon', <class 'netCDF4._netCDF4.Variable'>
float64 lon(lon)
    standard_name: longitude
    long_name: longitude
    units: degrees_east
    axis: X
unlimited dimensions: 
current shape = (700,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lat', <class 'netCDF4._netCDF4.Variable'>
float64 lat(lat)
    standard_name: latitude
    long_name: latitude
    units: degrees_north
    axis: Y
unlimited dimensions: 
current shape = (400,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('height', <class 'netCDF4._netCDF4.Variable'>
float64 height(height)
    standard_name: height
    long_name: height
    units: m
   

...

OrderedDict([('time', <class 'netCDF4._netCDF4.Variable'>
float64 time(time)
    standard_name: time
    units: hours since 2015-10-5 00:00:00
    calendar: proleptic_gregorian
    axis: T
    long_name: FORECAST time from 20151005
unlimited dimensions: time
current shape = (25,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lon', <class 'netCDF4._netCDF4.Variable'>
float64 lon(lon)
    standard_name: longitude
    long_name: longitude
    units: degrees_east
    axis: X
unlimited dimensions: 
current shape = (700,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lat', <class 'netCDF4._netCDF4.Variable'>
float64 lat(lat)
    standard_name: latitude
    long_name: latitude
    units: degrees_north
    axis: Y
unlimited dimensions: 
current shape = (400,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('height', <class 'netCDF4._netCDF4.Variable'>
float64 height(height)
    standard_name: height
    long_name: height
    units: m
   

OrderedDict([('time', <class 'netCDF4._netCDF4.Variable'>
float64 time(time)
    standard_name: time
    units: hours since 2015-10-5 00:00:00
    calendar: proleptic_gregorian
    axis: T
    long_name: FORECAST time from 20151005
unlimited dimensions: time
current shape = (25,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lon', <class 'netCDF4._netCDF4.Variable'>
float64 lon(lon)
    standard_name: longitude
    long_name: longitude
    units: degrees_east
    axis: X
unlimited dimensions: 
current shape = (700,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lat', <class 'netCDF4._netCDF4.Variable'>
float64 lat(lat)
    standard_name: latitude
    long_name: latitude
    units: degrees_north
    axis: Y
unlimited dimensions: 
current shape = (400,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('height', <class 'netCDF4._netCDF4.Variable'>
float64 height(height)
    standard_name: height
    long_name: height
    units: m
   

OrderedDict([('time', <class 'netCDF4._netCDF4.Variable'>
float64 time(time)
    standard_name: time
    units: hours since 2015-10-5 00:00:00
    calendar: proleptic_gregorian
    axis: T
    long_name: FORECAST time from 20151005
unlimited dimensions: time
current shape = (25,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lon', <class 'netCDF4._netCDF4.Variable'>
float64 lon(lon)
    standard_name: longitude
    long_name: longitude
    units: degrees_east
    axis: X
unlimited dimensions: 
current shape = (700,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lat', <class 'netCDF4._netCDF4.Variable'>
float64 lat(lat)
    standard_name: latitude
    long_name: latitude
    units: degrees_north
    axis: Y
unlimited dimensions: 
current shape = (400,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('height', <class 'netCDF4._netCDF4.Variable'>
float64 height(height)
    standard_name: height
    long_name: height
    units: m
   

OrderedDict([('time', <class 'netCDF4._netCDF4.Variable'>
float64 time(time)
    standard_name: time
    units: hours since 2015-10-5 00:00:00
    calendar: proleptic_gregorian
    axis: T
    long_name: FORECAST time from 20151005
unlimited dimensions: time
current shape = (25,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lon', <class 'netCDF4._netCDF4.Variable'>
float64 lon(lon)
    standard_name: longitude
    long_name: longitude
    units: degrees_east
    axis: X
unlimited dimensions: 
current shape = (700,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lat', <class 'netCDF4._netCDF4.Variable'>
float64 lat(lat)
    standard_name: latitude
    long_name: latitude
    units: degrees_north
    axis: Y
unlimited dimensions: 
current shape = (400,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('height', <class 'netCDF4._netCDF4.Variable'>
float64 height(height)
    standard_name: height
    long_name: height
    units: m
   

OrderedDict([('time', <class 'netCDF4._netCDF4.Variable'>
float64 time(time)
    standard_name: time
    units: hours since 2015-10-5 00:00:00
    calendar: proleptic_gregorian
    axis: T
    long_name: FORECAST time from 20151005
unlimited dimensions: time
current shape = (25,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lon', <class 'netCDF4._netCDF4.Variable'>
float64 lon(lon)
    standard_name: longitude
    long_name: longitude
    units: degrees_east
    axis: X
unlimited dimensions: 
current shape = (700,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('lat', <class 'netCDF4._netCDF4.Variable'>
float64 lat(lat)
    standard_name: latitude
    long_name: latitude
    units: degrees_north
    axis: Y
unlimited dimensions: 
current shape = (400,)
filling on, default _FillValue of 9.969209968386869e+36 used
), ('height', <class 'netCDF4._netCDF4.Variable'>
float64 height(height)
    standard_name: height
    long_name: height
    units: m
   